<a href="https://colab.research.google.com/github/Klfrr/Fine-Tune-W2V2-Classifier-for-Chinese-Accents/blob/main/hong_project.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Wav2Vec2 Fine Tuning
by Kalista Hong
- Uses an A100 GPU from Google Colab
High-RAM

In [ ]:
pip install torchcodec

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 46.7 MB/s eta 0:00:00


In [ ]:
import torch
import torchaudio
import torchcodec
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
from collections import defaultdict

In [ ]:
pip install seaborn

In [ ]:
import numpy as np
import random
import json
from pathlib import Path
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, confusion_matrix
import seaborn as sns

In [ ]:
import os
import pandas as pd

In [ ]:
import transformers
from transformers import Wav2Vec2Processor, Wav2Vec2ForSequenceClassification, AutoConfig
from torch.utils.data import Dataset, DataLoader
import librosa

In [ ]:
# Memory Management
import gc

In [ ]:
target_sample_rate = 16000

In [ ]:
# Load model and processor
model_name = "vrund1346/wav2vec2_accent_classification_v2"
processor = Wav2Vec2Processor.from_pretrained("facebook/wav2vec2-base")
model = Wav2Vec2ForSequenceClassification.from_pretrained(model_name)

config = AutoConfig.from_pretrained(model_name)

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


preprocessor_config.json:   0%|          | 0.00/159 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/163 [00:00<?, ?B/s]

config.json: 0.00B [00:00, ?B/s]

/usr/local/lib/python3.12/dist-packages/transformers/configuration_utils.py:335: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(


vocab.json:   0%|          | 0.00/291 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/85.0 [00:00<?, ?B/s]

config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/378M [00:00<?, ?B/s]

In [ ]:
_AUDIO_DIR = "SpeechAccentArchive" # May need to be changed for non-Google Colab

#SAMPLE_MP3_PATH = os.path.join(_AUDIO_DIR, "mandarin4.mp3")
#SAMPLE_MP3_PATH = "cantonese4.mp3"

os.makedirs(_AUDIO_DIR, exist_ok=True)

Uploading SpeechAccentArchive.zip

In [ ]:
# Mount Drive
#Not Neccessary if the model is running once
from google.colab import drive
drive.mount('/content/drive')

MessageError: Error: credential propagation was unsuccessful

In [ ]:
# Use if running once
from google.colab import files

# Opens a file picker for the audio files
uploaded = files.upload()

for filename in uploaded.keys():
    print("Uploaded file:", filename)

Saving SpeechAccentArchive.zip to SpeechAccentArchive.zip
Uploaded file: SpeechAccentArchive.zip


In [ ]:
!unzip SpeechAccentArchive.zip

Archive:  SpeechAccentArchive.zip
  inflating: SpeechAccentArchive/cantonese1.mp3  
  inflating: SpeechAccentArchive/cantonese10.mp3  
  inflating: SpeechAccentArchive/cantonese11.mp3  
  inflating: SpeechAccentArchive/cantonese12.mp3  
  inflating: SpeechAccentArchive/cantonese13.mp3  
  inflating: SpeechAccentArchive/cantonese14.mp3  
  inflating: SpeechAccentArchive/cantonese15.mp3  
  inflating: SpeechAccentArchive/cantonese16.mp3  
  inflating: SpeechAccentArchive/cantonese17.mp3  
  inflating: SpeechAccentArchive/cantonese18.mp3  
  inflating: SpeechAccentArchive/cantonese19.mp3  
  inflating: SpeechAccentArchive/cantonese2.mp3  
  inflating: SpeechAccentArchive/cantonese20.mp3  
  inflating: SpeechAccentArchive/cantonese21.mp3  
  inflating: SpeechAccentArchive/cantonese22.mp3  
  inflating: SpeechAccentArchive/cantonese23.mp3  
  inflating: SpeechAccentArchive/cantonese24.mp3  
  inflating: SpeechAccentArchive/cantonese25.mp3  
  inflating: SpeechAccentArchive/cantonese26.mp3  

Next cells are only for single samples

In [ ]:
# @title
# Load audio file
#waveform, sample_rate = torchaudio.load(SAMPLE_MP3_PATH)
# By default, dtype=torch.float32 and range is normalized within [-1.0, 1.0]
#print("Waveform shape:", waveform.shape)
#print("Sample rate:", sample_rate)

Waveform shape: torch.Size([1, 1553290])
Sample rate: 44100


In [ ]:
# @title
# Play audio
from IPython.display import Audio, display
def play_audio(waveform, sample_rate):
  waveform = waveform.numpy()

  num_channels, num_frames = waveform.shape
  if num_channels == 1:
    display(Audio(waveform[0], rate=sample_rate))
  elif num_channels == 2:
    display(Audio((waveform[0], waveform[1]), rate=sample_rate))
  else:
    raise ValueError("Waveform with more than 2 channels are not supported.")

play_audio(waveform, sample_rate)

In [ ]:
# @title
# Save audio (Optional)
path = f"{_AUDIO_DIR}/save_example_default.wav"
torchaudio.save(path, waveform, sample_rate, encoding="PCM_S", bits_per_sample=16, format="wav")

In [ ]:
# @title
# Convert to mono if necessary
if waveform.shape[0] > 1:
    waveform = waveform.mean(dim=0)
    print("Converted to mono")
else:
    waveform = waveform.squeeze(0)

In [ ]:
# @title
# Check Sample Rate and convert if necessary
target_sample_rate = 16000
if sample_rate != target_sample_rate:
    resampler = torchaudio.transforms.Resample(orig_freq=sample_rate, new_freq=target_sample_rate)
    waveform = resampler(waveform)
    sample_rate = target_sample_rate

In [ ]:
# @title
input_values = processor(waveform, return_tensors="pt", sampling_rate=target_sample_rate).input_values

In [ ]:
# @title
# Predict Accent
with torch.no_grad():
    logits = model(input_values).logits
predicted_accent = torch.argmax(logits, dim=-1).item()
label_map = getattr(model.config, "id2label", None) or {}
predicted_label = label_map.get(predicted_accent, str(predicted_accent))
print("Predicted Accent:", predicted_label)

Predicted Accent: LABEL_0


In [ ]:
# @title
# Print Log Liklihood
log_probs = torch.softmax(logits, dim=-1)

# Print top probability only:
log_likelihood = log_probs[0][predicted_accent].item()
print(f"Log-Likelihood: {log_likelihood}")

# Print top 3 probablilities
#top3_probs, top3_indices = torch.topk(log_probs[0], k=3)
#print(f"Log-Likelihood of the top 3: {top3_probs[0]}, {top3_probs[1]}, {top3_probs[2]}")

SyntaxError: unterminated f-string literal (detected at line 6) (ipython-input-2733804313.py, line 6)

Evaluate the Current Model Wav2Vec2

In [ ]:
# @title
# Get label mapping from model config
label_map = getattr(model.config, "id2label", None) or {}
# Create reverse mapping for display
id_to_label = {int(k): v for k, v in label_map.items()}

# Define the 11 accent labels in order
accent_labels = ["Arabic", "Dutch", "English", "French", "German", "Korean",
                 "Mandarin", "Portuguese", "Russian", "Spanish", "Turkish"]

# Group audio files by accent type based on filename prefix
audio_files = [f for f in os.listdir(_AUDIO_DIR) if f.endswith('.mp3')]

accent_groups = {
    'Cantonese': [],
    'Mandarin': [],
    'Taiwanese': [],
    'Wu': []
}

for audio_file in audio_files:
    filename_lower = audio_file.lower()
    if filename_lower.startswith('cantonese'):
        accent_groups['Cantonese'].append(audio_file)
    elif filename_lower.startswith('mandarin'):
        accent_groups['Mandarin'].append(audio_file)
    elif filename_lower.startswith('taiwanese'):
        accent_groups['Taiwanese'].append(audio_file)
    elif filename_lower.startswith('wu'):
        accent_groups['Wu'].append(audio_file)

# Dictionary to store predictions: {accent_group: {predicted_label}}
predictions_by_group = {
    'Cantonese': defaultdict(int),
    'Mandarin': defaultdict(int),
    'Taiwanese': defaultdict(int),
    'Wu': defaultdict(int)
}

In [ ]:
# @title
# Create a mapping from LABEL_X format to accent names
# If model returns LABEL_0, LABEL_1, etc., map them by index
label_x_to_accent = {}
for i, accent in enumerate(accent_labels):
    label_x_to_accent[f"LABEL_{i}"] = accent
    label_x_to_accent[f"label_{i}"] = accent  # lowercase variant

In [ ]:
# @title
# Create a mapping from model labels to our accent_labels (case-insensitive)
def normalize_label(label):
    """Normalize label to match accent_labels list"""
    label_str = str(label).strip()

    # First, try direct LABEL_X mapping
    if label_str in label_x_to_accent:
        return label_x_to_accent[label_str]

    # Try case-insensitive LABEL_X matching
    label_upper = label_str.upper()
    if label_upper in label_x_to_accent:
        return label_x_to_accent[label_upper]

    # Try extracting number from LABEL_X format
    if label_str.startswith("LABEL_") or label_str.startswith("label_"):
        try:
            label_num = int(label_str.split("_")[-1])
            if 0 <= label_num < len(accent_labels):
                return accent_labels[label_num]
        except (ValueError, IndexError):
            pass

    # Try case-insensitive matching with accent names
    label_lower = label_str.lower()
    for accent in accent_labels:
        if accent.lower() == label_lower:
            return accent

    # If no match, return original (for debugging)
    return label_str

In [ ]:
# @title
# Dictionary to store log likelihoods for each sample: {accent_group: [log_likelihoods]}
log_likelihoods_by_group = {
    'Cantonese': [],
    'Mandarin': [],
    'Taiwanese': [],
    'Wu': []
}

In [ ]:
# @title
print("\nProcessing audio files...")
target_sample_rate = 16000
for accent_group, files in accent_groups.items():
    print(f"Processing {accent_group} files...")
    for audio_file in files:
        try:
            audio_path = os.path.join(_AUDIO_DIR, audio_file)
            waveform, sample_rate = torchaudio.load(audio_path)

            # Convert to mono if necessary
            if waveform.shape[0] > 1:
                waveform = waveform.mean(dim=0)
            else:
                waveform = waveform.squeeze(0)

            # Resample if necessary
            if sample_rate != target_sample_rate:
                resampler = torchaudio.transforms.Resample(orig_freq=sample_rate, new_freq=target_sample_rate)
                waveform = resampler(waveform)

            # Process and predict
            input_values = processor(waveform, return_tensors="pt", sampling_rate=target_sample_rate).input_values

            with torch.no_grad():
                logits = model(input_values).logits

            # Get predicted class
            predicted_accent_id = torch.argmax(logits, dim=-1).item()

            # Get the logit value (raw log likelihood) of the predicted class for this individual sample
            # This is the unnormalized log probability before softmax
            sample_log_likelihood = logits[0, predicted_accent_id].item()

            # Store log likelihood for this individual sample
            log_likelihoods_by_group[accent_group].append(sample_log_likelihood)

            # Get predicted label name
            predicted_label = id_to_label.get(predicted_accent_id, f"Unknown_{predicted_accent_id}")

            # If id_to_label doesn't have the mapping, use LABEL_X format
            if predicted_label is None:
                predicted_label = f"LABEL_{predicted_accent_id}"

            # Normalize label to match accent_labels
            normalized_label = normalize_label(predicted_label)

            # Store prediction with normalized label
            predictions_by_group[accent_group][normalized_label] += 1

        except Exception as e:
            print(f"Error processing {audio_file}: {e}")
            continue
print("Processing Complete.")


Processing audio files...
Processing Cantonese files...
Processing Mandarin files...
Processing Taiwanese files...
Processing Wu files...
Processing Complete.


In [ ]:
# @title
# Debug: Print model labels
#print(f"Model labels: {id_to_label}")
#print(f"Model label mapping: {label_map}")

In [ ]:
# @title
# Debug: Check the counts to see if there are predictions stored
for idx, accent_group in enumerate(['Cantonese', 'Mandarin', 'Taiwanese', 'Wu']):
  # Get counts for each of the 11 accent labels
  counts = [predictions_by_group[accent_group].get(label, 0) for label in accent_labels]
  # Check if we have any data
  total_count = sum(counts)
  if total_count == 0:
    print(f"  WARNING: No matching predictions found for {accent_group}!")
    print(f"  Actual predictions stored: {dict(predictions_by_group[accent_group])}")
  else:
    print(f"  Total files processed: {total_count}")

  Total files processed: 36
  Total files processed: 154
  Total files processed: 11
  Total files processed: 6


In [ ]:
# @title
# Show Results Visualization
# Create bar graphs for each accent group
fig, axes = plt.subplots(2, 2, figsize=(16, 12))
axes = axes.flatten()

for idx, accent_group in enumerate(['Cantonese', 'Mandarin', 'Taiwanese', 'Wu']):
    ax = axes[idx]

    # Get counts for each of the 11 accent labels
    counts = [predictions_by_group[accent_group].get(label, 0) for label in accent_labels]

    # Debug: Print counts for this group
    #print(f"\n{accent_group} - Counts for each label:")
    #for label, count in zip(accent_labels, counts):
    #    if count > 0:
    #        print(f"  {label}: {count}")

    # Debug: Check if we have any data
    total_count = sum(counts)
    if total_count == 0:
        print(f"  WARNING: No matching predictions found for {accent_group}!")
        print(f"  Actual predictions stored: {dict(predictions_by_group[accent_group])}")


    # Create bar graph
    bars = ax.bar(accent_labels, counts, color='steelblue', edgecolor='black')

    ax.set_xlabel('Predicted Accent', fontsize=10)
    ax.set_ylabel('Count of Audio Samples', fontsize=10)
    ax.set_title(f'{accent_group} - Distribution of Predicted Accents', fontsize=12, fontweight='bold')

    ax.set_xticks(range(len(accent_labels)))
    ax.set_xticklabels(accent_labels, rotation=45, ha='right')
    ax.grid(axis='y', alpha=0.3, linestyle='--')

    # Add value labels on top of bars
    for bar in bars:
        height = bar.get_height()
        if height > 0:
            ax.text(bar.get_x() + bar.get_width()/2., height,
                   f'{int(height)}',
                   ha='center', va='bottom', fontsize=8)

plt.tight_layout()
plt.savefig('accent_classification_results.png', dpi=300, bbox_inches='tight')
print("\nBar graphs saved as 'accent_classification_results.png'")
plt.show()

# Print summary statistics
print("\n" + "="*60)
print("SUMMARY STATISTICS")
print("="*60)
for accent_group in ['Cantonese', 'Mandarin', 'Taiwanese', 'Wu']:
    print(f"\n{accent_group}:")
    total = sum(predictions_by_group[accent_group].values())
    #print(f"  Total files processed: ")
    for label in accent_labels:
        count = predictions_by_group[accent_group].get(label, 0)
        if count > 0:
            percentage = (count / total) * 100
            print(f"  {label}: {count} ({percentage:.1f}%)")


Bar graphs saved as 'accent_classification_results.png'



SUMMARY STATISTICS

Cantonese:
  Arabic: 4 (11.1%)
  Dutch: 3 (8.3%)
  English: 7 (19.4%)
  Korean: 2 (5.6%)
  Mandarin: 13 (36.1%)
  Portuguese: 1 (2.8%)
  Russian: 1 (2.8%)
  Spanish: 4 (11.1%)
  Turkish: 1 (2.8%)

Mandarin:
  Arabic: 8 (5.2%)
  English: 2 (1.3%)
  French: 2 (1.3%)
  German: 1 (0.6%)
  Korean: 27 (17.5%)
  Mandarin: 101 (65.6%)
  Spanish: 9 (5.8%)
  Turkish: 4 (2.6%)

Taiwanese:
  Arabic: 1 (9.1%)
  English: 1 (9.1%)
  Korean: 5 (45.5%)
  Mandarin: 3 (27.3%)
  Spanish: 1 (9.1%)

Wu:
  Korean: 2 (33.3%)
  Mandarin: 3 (50.0%)
  Turkish: 1 (16.7%)


In [ ]:
# @title
# Label	Accent
#0	Arabic
#1	Dutch
#2	English
#3	French
#4	German
#5	Korean
#6	Mandarin
#7	Portuguese
#8	Russian
#9	Spanish
#10	Turkish

In [ ]:
# @title
# Debug: Check if the log likelihood has data
for accent_group in ['Cantonese', 'Mandarin', 'Taiwanese', 'Wu']:
  print(f"\n{accent_group} - Log Likelihoods:")
  print(log_likelihoods_by_group[accent_group])


Cantonese - Log Likelihoods:
[8.610736846923828, 9.107064247131348, 9.384509086608887, 8.855592727661133, 6.515716075897217, 6.864455223083496, 7.771218299865723, 9.524706840515137, 9.043421745300293, 9.047636985778809, 8.770329475402832, 9.55625057220459, 8.441519737243652, 8.231255531311035, 8.697633743286133, 9.536952018737793, 9.509096145629883, 9.526955604553223, 6.4115753173828125, 8.911528587341309, 9.97331428527832, 6.1215105056762695, 8.612242698669434, 9.486844062805176, 9.549707412719727, 7.590609073638916, 9.386395454406738, 8.997163772583008, 8.73540210723877, 8.630074501037598, 9.30555248260498, 9.542130470275879, 7.627665996551514, 9.392504692077637, 6.829354286193848, 6.267324447631836]

Mandarin - Log Likelihoods:
[9.530413627624512, 7.193060398101807, 9.344392776489258, 9.532660484313965, 9.402118682861328, 9.525792121887207, 9.355462074279785, 9.532187461853027, 9.531950950622559, 9.55429744720459, 9.887749671936035, 9.513282775878906, 9.526718139648438, 9.525559425

In [ ]:
# @title
# Print statistics for each group
print("\nLog Likelihood Statistics:")
for accent_group in ['Cantonese', 'Mandarin', 'Taiwanese', 'Wu']:
    if log_likelihoods_by_group[accent_group]:
        mean_ll = np.mean(log_likelihoods_by_group[accent_group])
        print(f"{accent_group}: Mean = {mean_ll:.4f}, Samples = {len(log_likelihoods_by_group[accent_group])}")


Log Likelihood Statistics:
Cantonese: Mean = 8.5657, Samples = 36
Mandarin: Mean = 9.2486, Samples = 154
Taiwanese: Mean = 9.0911, Samples = 11
Wu: Mean = 9.4112, Samples = 6


In [ ]:
# @title
# Create dataframe for boxplot
plot_data = []
for accent_group in ['Cantonese', 'Mandarin', 'Taiwanese', 'Wu']:
    for log_likelihood in log_likelihoods_by_group[accent_group]:
        plot_data.append({
            'Group': accent_group,
            'LogLikelihood': log_likelihood
        })

df = pd.DataFrame(plot_data)

# Create box and whisker plot using seaborn
plt.figure(figsize=(10, 6))
ax = sns.boxplot(data=df, x='Group', y='LogLikelihood', showmeans=True, meanprops={'marker':'D', 'markerfacecolor':'red', 'markeredgecolor':'red', 'markersize':8})
plt.title('Log Likelihood Distribution by Accent Group')
plt.xlabel('Accent Group')
plt.ylabel('Log Likelihood')
plt.xticks(rotation=45)
plt.tight_layout()
plt.savefig('log-liklihood_results.png', dpi=300, bbox_inches='tight')
plt.show()

In [ ]:
plt.savefig('log-liklihood_results.png', dpi=300, bbox_inches='tight')

<Figure size 640x480 with 0 Axes>

Fine Tuning Wav2Vec2

In [ ]:
OUTPUT_DIR = "training_output"
NUM_RANDOM_SEARCH_TRIALS = 10
RANDOM_SEED = 42

# Create output directory
Path(OUTPUT_DIR).mkdir(parents=True, exist_ok=True)

In [ ]:
# Set random seeds for reproducibility
torch.manual_seed(RANDOM_SEED)
np.random.seed(RANDOM_SEED)
random.seed(RANDOM_SEED)
if torch.cuda.is_available():
    torch.cuda.manual_seed_all(RANDOM_SEED)

In [ ]:
# Label mapping for 4 accent categories
ACCENT_LABELS = ['Cantonese', 'Mandarin', 'Taiwanese', 'Wu']
LABEL_TO_ID = {label: idx for idx, label in enumerate(ACCENT_LABELS)}
ID_TO_LABEL = {idx: label for label, idx in LABEL_TO_ID.items()}
NUM_CLASSES = len(ACCENT_LABELS)

In [ ]:
def load_and_process_audio(audio_path, processor, target_sample_rate=16000):
    """
    Load and process audio file for wav2vec2 model.
    Reuses existing processing logic.

    Args:
        audio_path: Path to audio file
        processor: Wav2Vec2Processor instance
        target_sample_rate: Target sample rate (default 16000)

    Returns:
        input_values: Processed audio
    """
    # Load audio
    waveform, sample_rate = torchaudio.load(audio_path)

    #label_upper = label_str.upper()
    #if label_upper in label_x_to_accent:
    #    return label_x_to_accent[label_upper]


    # Convert to mono if necessary
    if waveform.shape[0] > 1:
        waveform = waveform.mean(dim=0)
    else:
        waveform = waveform.squeeze(0)

    # Resample if necessary
    if sample_rate != target_sample_rate:
        resampler = torchaudio.transforms.Resample(orig_freq=sample_rate, new_freq=target_sample_rate)
        waveform = resampler(waveform)

    # Process with processor to get input_values
    input_values = processor(waveform, return_tensors="pt", sampling_rate=target_sample_rate).input_values

        # Process with processor to get input_values
    input_values = processor(waveform, return_tensors="pt", sampling_rate=target_sample_rate).input_values

    return input_values.squeeze(0)  # Remove batch dimension

In [ ]:

def collate_fn(batch):
    """
    Custom collate function to handle variable-length audio sequences.

    Args:
        batch: list of samples

    Returns:
        input_values: Processed audio
        labels: Corresponding label ID
    """
    input_values = [item['input_values'] for item in batch]
    labels = torch.stack([item['labels'] for item in batch])

    # Pad input_values to same length (wav2vec2 expects padded sequences)
    # Find max length in batch
    max_len = max(iv.shape[-1] for iv in input_values)

    # Pad all sequences to max_len
    padded_inputs = []
    for iv in input_values:
        # iv shape is (seq_len,) after squeeze
        iv = iv.squeeze()
        if iv.dim() == 0:
            iv = iv.unsqueeze(0)
        current_len = iv.shape[0]
        if current_len < max_len:
            padding = torch.zeros(max_len - current_len)
            padded = torch.cat([iv, padding])
        else:
            padded = iv[:max_len]  # Truncate if longer (shouldn't happen)
        padded_inputs.append(padded)

    input_values_tensor = torch.stack(padded_inputs)

    return {
        'input_values': input_values_tensor,
        'labels': labels
    }

In [ ]:
class AccentDataset(Dataset):
    """PyTorch Dataset for accent classification."""

    def __init__(self, file_paths, labels, processor, target_sample_rate=16000):
        """
        Args:
            file_paths: List of audio file paths
            labels: List of label IDs (integers 0-3)
            processor: Wav2Vec2Processor instance
            target_sample_rate: Target sample rate

        Returns:
            input_values: Processed audio
            labels: Corresponding label ID
        """
        self.file_paths = file_paths
        self.labels = labels
        self.processor = processor
        self.target_sample_rate = target_sample_rate

    def __len__(self):
        return len(self.file_paths)

    def __getitem__(self, idx):
        audio_path = self.file_paths[idx]
        label = self.labels[idx]

        input_values = load_and_process_audio(audio_path, self.processor, self.target_sample_rate)

        return {
            'input_values': input_values,
            'labels': torch.tensor(label, dtype=torch.long)
        }

Data Loading and Splitting

In [ ]:
def load_audio_files(audio_dir):
    """Load and group audio files by accent type.

        Args:
        audio_dir: Directory containing audio files

        Returns:
        accent_groups: Dictionary mapping accent names to list of file paths
        """
    audio_files = [f for f in os.listdir(audio_dir) if f.endswith('.mp3')]

    accent_groups = {
        'Cantonese': [],
        'Mandarin': [],
        'Taiwanese': [],
        'Wu': []
    }

    for audio_file in audio_files:
        filename_lower = audio_file.lower()
        if filename_lower.startswith('cantonese'):
            accent_groups['Cantonese'].append(os.path.join(audio_dir, audio_file))
        elif filename_lower.startswith('mandarin'):
            accent_groups['Mandarin'].append(os.path.join(audio_dir, audio_file))
        elif filename_lower.startswith('taiwanese'):
            accent_groups['Taiwanese'].append(os.path.join(audio_dir, audio_file))
        elif filename_lower.startswith('wu'):
            accent_groups['Wu'].append(os.path.join(audio_dir, audio_file))

    return accent_groups

In [ ]:
def create_datasets(audio_dir, processor, train_ratio=0.6, dev_ratio=0.2, test_ratio=0.2):
    """
    Create train/dev/test datasets with 60/20/20 split.

    Args:
        audio_dir: Directory containing audio files
        processor: Wav2Vec2Processor instance
        train_ratio: Proportion for training set
        dev_ratio: Proportion for dev set
        test_ratio: Proportion for test set

    Returns:
        train_dataset, dev_dataset, test_dataset: The three datasets randomized and split
    """
    accent_groups = load_audio_files(audio_dir)

    # Combine all files with labels
    all_files = []
    all_labels = []

    for accent_name, file_paths in accent_groups.items():
        label_id = LABEL_TO_ID[accent_name]
        all_files.extend(file_paths)
        all_labels.extend([label_id] * len(file_paths))

    # First split: train vs (dev + test)
    train_files, temp_files, train_labels, temp_labels = train_test_split(
        all_files, all_labels,
        test_size=(dev_ratio + test_ratio),
        stratify=all_labels,
        random_state=RANDOM_SEED
    )

    # Second split: dev vs test
    dev_ratio_adjusted = dev_ratio / (dev_ratio + test_ratio)
    dev_files, test_files, dev_labels, test_labels = train_test_split(
        temp_files, temp_labels,
        test_size=(1 - dev_ratio_adjusted),
        stratify=temp_labels,
        random_state=RANDOM_SEED
    )

    # Create datasets
    train_dataset = AccentDataset(train_files, train_labels, processor, target_sample_rate)
    dev_dataset = AccentDataset(dev_files, dev_labels, processor, target_sample_rate)
    test_dataset = AccentDataset(test_files, test_labels, processor, target_sample_rate)

    print(f"\nDataset splits:")
    print(f"  Training: {len(train_dataset)} samples")
    print(f"  Dev: {len(dev_dataset)} samples")
    print(f"  Test: {len(test_dataset)} samples")

    return train_dataset, dev_dataset, test_dataset

Model Setup

In [ ]:
def create_model_architecture(num_labels=4, base_config=None, base_state_dict=None):
    """Create Wav2Vec2 model instance with a modified classification head.
    If base_config and base_state_dict are provided, it initializes with those weights.
    Otherwise, it loads from the pretrained model_name.

    Returns:
        model: Wav2Vec2ForSequenceClassification instance
        processor: Wav2Vec2Processor instance
    """
    model_name = "vrund1346/wav2vec2_accent_classification_v2"
    processor = Wav2Vec2Processor.from_pretrained("facebook/wav2vec2-base")


    if base_config and base_state_dict:
        print("Initializing model from provided config and state_dict...")
        model = Wav2Vec2ForSequenceClassification(base_config)

        # Load the base pretrained weights
        #model.load_state_dict(base_state_dict)

        # Filter out classifier weights to avoid shape mismatch
        # (classifier will be replaced with new 4-class classifier anyway)
        filtered_state_dict = {k: v for k, v in base_state_dict.items()
                              if not k.startswith('classifier.')}
        # Load the base pretrained weights (excluding classifier)
        model.load_state_dict(filtered_state_dict, strict=False)
    else:
        print("Loading model from pretrained checkpoint...")
        # This path should ideally only be taken once for the initial model
        model = Wav2Vec2ForSequenceClassification.from_pretrained(model_name)

    # Determine classifier input dimension
    classifier_input_dim = model.config.hidden_size
    if hasattr(model, 'classifier') and model.classifier is not None:
        classifier_input_dim = model.classifier.in_features
    elif hasattr(model, 'projector') and model.projector is not None:
        classifier_input_dim = model.projector.out_features if hasattr(model.projector, 'out_features') else model.config.hidden_size

    # Modify classification head for `num_labels` classes
    model.config.num_labels = num_labels
    model.classifier = nn.Linear(classifier_input_dim, num_labels)
    print(f"Created new classifier: {classifier_input_dim} -> {num_labels} classes")

    # Move model to device if specified (this should move all parameters including the new classifier)
    if device is not None:
        model = model.to(device)
        # Verify all model parameters are on the correct device
        for name, param in model.named_parameters():
            if param.device != device:
                #print(f"Warning: Parameter {name} is on {param.device}, moving to {device}")
                param.data = param.data.to(device)

    return model, processor

Training Functions

In [ ]:
def train_epoch(model, dataloader, optimizer, criterion, device):
    """Training for one epoch.

    Args:
        model: Wav2Vec2ForSequenceClassification instance
        dataloader: DataLoader instance
        optimizer: Optimizer instance
        criterion: Loss function
        device: torch.device instance

    Returns:
        avg_loss: Average loss
        accuracy: Accuracy
    """
    model.train()
    total_loss = 0
    correct = 0
    total = 0

    # Process in smaller chunks and clear cache frequently to save memory
    batch_count = 0
    clear_cache_frequency = 5  # Clear cache every N batches

    for batch in dataloader:
      # Zero gradients before forward pass to free optimizer memory
      optimizer.zero_grad(set_to_none=True)  # set_to_none=True is more memory efficient

      input_values = batch['input_values'].to(device, non_blocking=True)  # non_blocking transfer
      labels = batch['labels'].to(device, non_blocking=True)

      # Forward pass
      outputs = model(input_values)
      logits = outputs.logits
      loss = criterion(logits, labels)

      # Backward pass
      optimizer.zero_grad()
      loss.backward()
      optimizer.step()

      # Metrics
      total_loss += loss.item()
      predictions = torch.argmax(logits, dim=-1)
      correct += (predictions == labels).sum().item()
      total += labels.size(0)

      # Explicitly delete intermediate tensors to help with memory
      del input_values, labels, outputs, logits, loss, predictions

    # Synchronize and clear cache periodically
    if torch.cuda.is_available():
        torch.cuda.synchronize()
        torch.cuda.empty_cache()

    avg_loss = total_loss / len(dataloader)
    accuracy = correct / total
    return avg_loss, accuracy
    ''' # Memory Saver Version
        # optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        # Metrics
        # Compute before deleting tensors
        with torch.no_grad():  # no_grad for metric computation to save memory
            total_loss += loss.item()
            predictions = torch.argmax(logits, dim=-1)
            correct += (predictions == labels).sum().item()
            total += labels.size(0)

        # Delete intermediate tensors to save memory
        del input_values, labels, outputs, logits, loss, predictions

        batch_count += 1
        # Clear cache periodically during epoch, not just at end
        if batch_count % clear_cache_frequency == 0 and torch.cuda.is_available():
            torch.cuda.empty_cache()
    '''

In [ ]:
def validate(model, dataloader, criterion, device):
    """Validate on dev set.

    Args:
        model: Wav2Vec2ForSequenceClassification instance
        dataloader: DataLoader instance
        criterion: Loss function

    Returns:
        avg_loss: Average loss
        accuracy: Accuracy
        all_predictions: List of all predictions
        all_labels: List of all labels
    """
    model.eval()
    total_loss = 0
    all_predictions = []
    all_labels = []

    with torch.no_grad():
        for batch in dataloader:
            input_values = batch['input_values'].to(device)
            labels = batch['labels'].to(device)

            #input_values = batch['input_values'].to(device, non_blocking=True)
            #labels = batch['labels'].to(device, non_blocking=True)

            outputs = model(input_values)
            logits = outputs.logits
            loss = criterion(logits, labels)

            total_loss += loss.item()
            predictions = torch.argmax(logits, dim=-1)

            # Save to CPU
            all_predictions.extend(predictions.cpu().numpy())
            all_labels.extend(labels.cpu().numpy())

            # Delete GPU tensors to save memory
            del input_values, labels, outputs, logits, loss, predictions

    # Synchronize and clear cache after validation
    if torch.cuda.is_available():
        torch.cuda.synchronize()
        torch.cuda.empty_cache()

    avg_loss = total_loss / len(dataloader)
    accuracy = accuracy_score(all_labels, all_predictions)
    return avg_loss, accuracy, all_predictions, all_labels

Random Search Hyperparameter Tuning

In [ ]:
def sample_hyperparameters():
    """Sample hyperparameters from search space.

    Returns:
        hyperparams: Dictionary of sampled hyperparameters
    """
    # Learning rate: log-uniform between 1e-5 and 1e-2
    lr = 10 ** np.random.uniform(-5, -2)

    # Epsilon: [1e-8, 1e-7, 1e-6]
    eps = np.random.choice([1e-8, 1e-7, 1e-6])

    # Batch size: [1, 2, 4] - Reduced to avoid OOM
    batch_size = np.random.choice([1, 2, 4])

    # Weight decay: [0, 0.01, 0.001]
    weight_decay = np.random.choice([0.0, 0.01, 0.001])

    # Number of epochs (fixed or can be made searchable)
    num_epochs = 10  # Can be made searchable if needed

    return {
        'learning_rate': lr,
        'epsilon': eps,
        'batch_size': batch_size,
        'weight_decay': weight_decay,
        'num_epochs': num_epochs
    }

In [ ]:
def train_with_hyperparameters(base_config, base_state_dict, processor, train_dataset, dev_dataset, hyperparams, device):
    """Train model with given hyperparameters.

    Args:
        base_config: Wav2Vec2Config instance
        base_state_dict: State dict of base pretrained model
        processor: Wav2Vec2Processor instance
        train_dataset: Dataset instance
        dev_dataset: Dataset instance

      Returns:
        best_dev_accuracy: Best accuracy number of the dev set
        best_model_state: State dictionary of best model
    """
    # Clear GPU cache before starting
    if torch.cuda.is_available():
        torch.cuda.synchronize()
        torch.cuda.empty_cache()
        torch.cuda.reset_peak_memory_stats()  # Reset peak memory tracking

    """Train model with given hyperparameters."""
    # Create data loaders with collate function
    train_loader = DataLoader(
        train_dataset,
        batch_size=int(hyperparams['batch_size']), # Cast to int from numpy int
        shuffle=True,
        num_workers=0,  # Set to 0 to avoid multiprocessing issues
        collate_fn=collate_fn
    )
    dev_loader = DataLoader(
        dev_dataset,
        batch_size=int(hyperparams['batch_size']), # Cast to int from numpy int
        shuffle=False,
        num_workers=0,
        collate_fn=collate_fn
    )

    # Create a fresh model instance for this trial, initialized with base pretrained weights
    model_copy, model_processor = create_model_architecture(NUM_CLASSES, base_config=base_config, base_state_dict=base_state_dict)
    #model_copy = model_copy.to(device)

    # Clear cache after model creation
    if torch.cuda.is_available():
        torch.cuda.empty_cache()

    # Setup optimizer and criterion
    optimizer = torch.optim.Adagrad(
        model_copy.parameters(),
        lr=hyperparams['learning_rate'],
        eps=hyperparams['epsilon'],
        weight_decay=hyperparams['weight_decay']
    )
    criterion = nn.CrossEntropyLoss()

    # Training loop
    best_dev_accuracy = 0
    best_model_state = None
    training_history = []

    for epoch in range(hyperparams['num_epochs']):
        train_loss, train_acc = train_epoch(model_copy, train_loader, optimizer, criterion, device)
        dev_loss, dev_acc, _, _ = validate(model_copy, dev_loader, criterion, device)

        training_history.append({
            'epoch': epoch + 1,
            'train_loss': train_loss,
            'train_acc': train_acc,
            'dev_loss': dev_loss,
            'dev_acc': dev_acc
        })

        # Save best model
        if dev_acc > best_dev_accuracy:
            best_dev_accuracy = dev_acc
            best_model_state = model_copy.state_dict().copy()

        # Clear cache after each epoch to help with memory
        if torch.cuda.is_available():
            torch.cuda.synchronize()
            torch.cuda.empty_cache()

    # Explicitly delete model, optimizer, and dataloaders to free memory
    del model_copy, optimizer, train_loader, dev_loader, criterion
    if torch.cuda.is_available():
        torch.cuda.synchronize()  # Wait for all operations to complete
        gc.collect()
        torch.cuda.empty_cache()  # Release cached memory

    return best_dev_accuracy, best_model_state, training_history

In [ ]:
def random_search(processor, base_config, base_state_dict, train_dataset, dev_dataset, num_trials=NUM_RANDOM_SEARCH_TRIALS):
    """Perform random search for hyperparameters.

    Args:
        processor: Wav2Vec2Processor instance
        base_config: Wav2Vec2Config instance
        base_state_dict: State dict of base pretrained model
        train_dataset: Dataset instance
        dev_dataset: Dataset instance
        num_trials: Number of random search trials

    Returns:
        best_hyperparams: Dictionary of best hyperparameters
        best_model_state: State dicttionary of best model
    """
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    print(f"\nUsing device: {device}")

    results = []
    best_accuracy = 0
    best_hyperparams = None
    best_model_state = None

    print(f"\nStarting random search with {num_trials} trials...")

    for trial in range(num_trials):
        print(f"\n{'='*60}")
        print(f"Epoch {trial + 1}/{num_trials}")
        print(f"{'='*60}")

        # Sample hyperparameters
        hyperparams = sample_hyperparameters()
        print(f"Hyperparameters: {hyperparams}")

        # Train with these hyperparameters
        dev_accuracy, model_state, history = train_with_hyperparameters(
            base_config, base_state_dict, processor, train_dataset, dev_dataset, hyperparams, device
        )

        print(f"Best dev accuracy: {dev_accuracy:.4f}")

        # Save this trial's best model state to a file
        trial_model_path = os.path.join(OUTPUT_DIR, f'trial_{trial + 1}_best_model.pt')
        torch.save({
            'model_state_dict': model_state,
            'hyperparameters': hyperparams,
            'best_dev_accuracy': dev_accuracy,
            'num_classes': NUM_CLASSES,
            'label_to_id': LABEL_TO_ID
        }, trial_model_path)
        print(f"Trial {trial + 1} model saved to {trial_model_path}")

        # Store results
        result = {
            'trial': trial + 1,
            'hyperparameters': hyperparams,
            'best_dev_accuracy': dev_accuracy,
            'training_history': history,
            'model_path': trial_model_path
        }
        results.append(result)

        # Update best
        if dev_accuracy > best_accuracy:
            best_accuracy = dev_accuracy
            best_hyperparams = hyperparams
            best_model_state = model_state
            print(f"*** New best accuracy: {best_accuracy:.4f} ***")

        # Aggressive memory cleanup between trials
        if torch.cuda.is_available():
            gc.collect()
            torch.cuda.synchronize()  # Ensure all CUDA operations complete
            torch.cuda.empty_cache()  # Release cached (but not necessarily all reserved) memory
            # Print memory status
            allocated = torch.cuda.memory_allocated(0) / 1024**3
            reserved = torch.cuda.memory_reserved(0) / 1024**3
            print(f"Memory after trial {trial + 1}: {allocated:.2f} GB allocated, {reserved:.2f} GB reserved")
            #print(f"  (Note: Reserved memory may not decrease immediately due to PyTorch's memory caching)")

    return best_hyperparams, best_model_state, results

Main Training Pipeline

In [ ]:
"""Main training pipeline."""
print("="*60)
print("Wav2Vec2 Fine-tuning")
print("="*60)

# Load processor and base model config/state dict once
model_name = "vrund1346/wav2vec2_accent_classification_v2"
print("Loading base processor...")
processor = Wav2Vec2Processor.from_pretrained("facebook/wav2vec2-base")
print("Loading base pretrained model for configuration...")
base_pretrained_model = Wav2Vec2ForSequenceClassification.from_pretrained(model_name)
base_config = base_pretrained_model.config
base_state_dict = base_pretrained_model.state_dict()
# Explicitly delete to free memory before random search starts
del base_pretrained_model
if torch.cuda.is_available():
    torch.cuda.empty_cache()
    gc.collect()
print("Base model loaded and memory cleared.")

# Create datasets
train_dataset, dev_dataset, test_dataset = create_datasets(_AUDIO_DIR, processor)

# Random search for hyperparameters
best_hyperparams, best_model_state, search_results = random_search(
   processor, base_config, base_state_dict, train_dataset, dev_dataset, NUM_RANDOM_SEARCH_TRIALS
)

print(f"\n{'='*60}")
print("Random Search Complete")
print(f"{'='*60}")
print(f"Best hyperparameters: {best_hyperparams}")

# Save search results
results_path = os.path.join(OUTPUT_DIR, 'random_search_results.json')
with open(results_path, 'w') as f:
    # Convert numpy types to native Python types for JSON serialization
    json_results = []
    for result in search_results:
        json_result = {
            'trial': result['trial'],
            'hyperparameters': {
                k: float(v) if isinstance(v, (np.floating, float)) else int(v) if isinstance(v, (np.integer, int)) else v
                for k, v in result['hyperparameters'].items()
            },
            'best_dev_accuracy': float(result['best_dev_accuracy']),
            'training_history': [
                {
                    k: float(v) if isinstance(v, (np.floating, float)) else int(v) if isinstance(v, (np.integer, int)) else v
                    for k, v in hist.items()
                }
                for hist in result['training_history']
            ],
            'model_path': result.get('model_path', '')  # Include model path in JSON
        }
        json_results.append(json_result)
    json.dump(json_results, f, indent=2)
print(f"Search results saved to {results_path}")

Wav2Vec2 Fine-tuning
Loading base processor...
Loading base pretrained model for configuration...
Base model loaded and memory cleared.

Dataset splits:
  Training: 124 samples
  Dev: 41 samples
  Test: 42 samples

Using device: cuda

Starting random search with 10 trials...

Epoch 1/10
Hyperparameters: {'learning_rate': 0.0006358358856676251, 'epsilon': np.float64(1e-06), 'batch_size': np.int64(2), 'weight_decay': np.float64(0.0), 'num_epochs': 10}


/usr/local/lib/python3.12/dist-packages/transformers/configuration_utils.py:335: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(


Initializing model from provided config and state_dict...
Created new classifier: 256 -> 4 classes
Best dev accuracy: 0.7561
Trial 1 model saved to training_output/trial_1_best_model.pt
*** New best accuracy: 0.7561 ***
Memory after trial 1: 0.38 GB allocated, 0.45 GB reserved
  (Note: Reserved memory may not decrease immediately due to PyTorch's memory caching)

Epoch 2/10
Hyperparameters: {'learning_rate': 4.3329641750057214e-05, 'epsilon': np.float64(1e-06), 'batch_size': np.int64(1), 'weight_decay': np.float64(0.01), 'num_epochs': 10}


/usr/local/lib/python3.12/dist-packages/transformers/configuration_utils.py:335: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(


Initializing model from provided config and state_dict...
Created new classifier: 256 -> 4 classes
Best dev accuracy: 0.7805
Trial 2 model saved to training_output/trial_2_best_model.pt
*** New best accuracy: 0.7805 ***
Memory after trial 2: 0.38 GB allocated, 0.47 GB reserved
  (Note: Reserved memory may not decrease immediately due to PyTorch's memory caching)

Epoch 3/10
Hyperparameters: {'learning_rate': 0.0011288535257550282, 'epsilon': np.float64(1e-08), 'batch_size': np.int64(2), 'weight_decay': np.float64(0.0), 'num_epochs': 10}


...

Initializing model from provided config and state_dict...
Created new classifier: 256 -> 4 classes
Best dev accuracy: 0.7561
Trial 8 model saved to training_output/trial_8_best_model.pt
Memory after trial 8: 0.73 GB allocated, 0.96 GB reserved
  (Note: Reserved memory may not decrease immediately due to PyTorch's memory caching)

Epoch 9/10
Hyperparameters: {'learning_rate': 0.0008537217565195473, 'epsilon': np.float64(1e-08), 'batch_size': np.int64(4), 'weight_decay': np.float64(0.001), 'num_epochs': 10}


/usr/local/lib/python3.12/dist-packages/transformers/configuration_utils.py:335: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(


Initializing model from provided config and state_dict...
Created new classifier: 256 -> 4 classes
Best dev accuracy: 0.7561
Trial 9 model saved to training_output/trial_9_best_model.pt
Memory after trial 9: 0.73 GB allocated, 0.92 GB reserved
  (Note: Reserved memory may not decrease immediately due to PyTorch's memory caching)

Epoch 10/10
Hyperparameters: {'learning_rate': 4.9414649172553304e-05, 'epsilon': np.float64(1e-06), 'batch_size': np.int64(4), 'weight_decay': np.float64(0.001), 'num_epochs': 10}


/usr/local/lib/python3.12/dist-packages/transformers/configuration_utils.py:335: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(


Initializing model from provided config and state_dict...
Created new classifier: 256 -> 4 classes
Best dev accuracy: 0.8049
Trial 10 model saved to training_output/trial_10_best_model.pt
*** New best accuracy: 0.8049 ***
Memory after trial 10: 0.38 GB allocated, 0.65 GB reserved
  (Note: Reserved memory may not decrease immediately due to PyTorch's memory caching)

Random Search Complete
Best hyperparameters: {'learning_rate': 4.9414649172553304e-05, 'epsilon': np.float64(1e-06), 'batch_size': np.int64(4), 'weight_decay': np.float64(0.001), 'num_epochs': 10}
Search results saved to training_output/random_search_results.json


Evaluation Functions

In [ ]:
def evaluate_model(model, test_dataset, device, batch_size=16):
    """Evaluate model on test set with detailed metrics.

    Args:
        model: Wav2Vec2ForSequenceClassification instance
        test_dataset: Dataset instance
        device: torch.device instance
        batch_size: int

    Returns:
        metrics: Dictionary of evaluation metrics
        cm: Confusion matrix
    """
    test_loader = DataLoader(
        test_dataset,
        batch_size=batch_size,
        shuffle=False,
        num_workers=0,
        collate_fn=collate_fn
    )

    criterion = nn.CrossEntropyLoss()
    test_loss, test_accuracy, predictions, labels = validate(model, test_loader, criterion, device)

    # Calculate per-class metrics
    precision, recall, f1, support = precision_recall_fscore_support(
        labels, predictions, average=None, labels=list(range(NUM_CLASSES))
    )

    # Calculate macro and weighted averages
    precision_macro, recall_macro, f1_macro, _ = precision_recall_fscore_support(
        labels, predictions, average='macro'
    )
    precision_weighted, recall_weighted, f1_weighted, _ = precision_recall_fscore_support(
        labels, predictions, average='weighted'
    )

    # Confusion matrix
    cm = confusion_matrix(labels, predictions, labels=list(range(NUM_CLASSES)))

    metrics = {
        'test_loss': test_loss,
        'test_accuracy': test_accuracy,
        'per_class': {
            label: {
                'precision': float(precision[i]),
                'recall': float(recall[i]),
                'f1': float(f1[i]),
                'support': int(support[i])
            }
            for i, label in enumerate(ACCENT_LABELS)
        },
        'macro_avg': {
            'precision': float(precision_macro),
            'recall': float(recall_macro),
            'f1': float(f1_macro)
        },
        'weighted_avg': {
            'precision': float(precision_weighted),
            'recall': float(recall_weighted),
            'f1': float(f1_weighted)
        }
    }

    return metrics, cm

In [ ]:
def plot_confusion_matrix(cm, labels, save_path):
    """Plot and save confusion matrix.

    Args:
        cm (numpy.ndarray): Confusion matrix.
        labels (list): List of accent labels.
    """
    plt.figure(figsize=(8, 6))
    sns.heatmap(cm, annot=True, fmt='d', cmap='Blues', xticklabels=labels, yticklabels=labels)
    plt.title('Confusion Matrix')
    plt.ylabel('True Label')
    plt.xlabel('Predicted Label')
    plt.tight_layout()
    plt.savefig(save_path, dpi=300)
    print(f"Confusion matrix saved to {save_path}")
    plt.close()

In [ ]:
from regex import W
"""Evaluation pipeline."""
print("="*60)
print("Evaluation of Tuned Wav2vec2")
print("="*60)

'''# Load processor and base model config/state dict once
    model_name = "vrund1346/wav2vec2_accent_classification_v2"
    print("Loading base processor...")
    processor = Wav2Vec2Processor.from_pretrained("facebook/wav2vec2-base")
    print("Loading base pretrained model for configuration...")
    base_pretrained_model = Wav2Vec2ForSequenceClassification.from_pretrained(model_name)
    base_config = base_pretrained_model.config
    base_state_dict = base_pretrained_model.state_dict()
    # Explicitly delete to free memory before random search starts
    del base_pretrained_model
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
        gc.collect()
    print("Base model loaded and memory cleared.")

    # Create datasets
    train_dataset, dev_dataset, test_dataset = create_datasets(_AUDIO_DIR, processor)

    # Random search for hyperparameters
    best_hyperparams, best_model_state, search_results = random_search(
        processor, base_config, base_state_dict, train_dataset, dev_dataset, NUM_RANDOM_SEARCH_TRIALS
    )
'''
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Load best model from JSON file
print(f"\nLoading best model from JSON results...")
results_path = os.path.join(OUTPUT_DIR, 'random_search_results.json')
with open(results_path, 'r') as f:
  json_results = json.load(f)

# Find the trial with the highest best_dev_accuracy
best_trial = max(json_results, key=lambda x: x['best_dev_accuracy'])
best_model_path = best_trial['model_path']
best_hyperparams = best_trial['hyperparameters']

print(f"Best trial: {best_trial['trial']} with accuracy: {best_trial['best_dev_accuracy']:.4f}")
print(f"Loading model from: {best_model_path}")

# Load the model checkpoint
checkpoint = torch.load(best_model_path, map_location=device, weights_only=False) # Set weights_only to false since they are created weights
final_model_state = checkpoint['model_state_dict']

# Create model and load state
final_model, _ = create_model_architecture(NUM_CLASSES, device)
final_model.load_state_dict(final_model_state)

# Clear GPU cache
#torch.cuda.empty_cache()

# Final evaluation on test set
print(f"\n{'='*60}")
print("Final Evaluation on Test Set")
print(f"{'='*60}")
metrics, cm = evaluate_model(final_model, test_dataset, device, batch_size=best_hyperparams['batch_size'])

# Print metrics
print(f"\nTest Loss: {metrics['test_loss']:.4f}")
print(f"Test Accuracy: {metrics['test_accuracy']:.4f}")
print(f"\nPer-class metrics:")
for label, class_metrics in metrics['per_class'].items():
    print(f"  {label}:")
    print(f"    Precision: {class_metrics['precision']:.4f}")
    print(f"    Recall: {class_metrics['recall']:.4f}")
    print(f"    F1: {class_metrics['f1']:.4f}")
    print(f"    Support: {class_metrics['support']}")
print(f"\nMacro averages:")
print(f"  Precision: {metrics['macro_avg']['precision']:.4f}")
print(f"  Recall: {metrics['macro_avg']['recall']:.4f}")
print(f"  F1: {metrics['macro_avg']['f1']:.4f}")
print(f"\nWeighted averages:")
print(f"  Precision: {metrics['weighted_avg']['precision']:.4f}")
print(f"  Recall: {metrics['weighted_avg']['recall']:.4f}")
print(f"  F1: {metrics['weighted_avg']['f1']:.4f}")

# Save metrics
metrics_path = os.path.join(OUTPUT_DIR, 'test_metrics.json')
with open(metrics_path, 'w') as f:
    json.dump(metrics, f, indent=2)
print(f"\nMetrics saved to {metrics_path}")

# Plot confusion matrix
cm_path = os.path.join(OUTPUT_DIR, 'confusion_matrix.png')
plot_confusion_matrix(cm, ACCENT_LABELS, cm_path)

print(f"\n{'='*60}")
print("Process Complete!")
print(f"{'='*60}")

Evaluation of Tuned Wav2vec2

Loading best model from JSON results...
Best trial: 10 with accuracy: 0.8049
Loading model from: training_output/trial_10_best_model.pt


/usr/local/lib/python3.12/dist-packages/transformers/configuration_utils.py:335: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(


Loading model from pretrained checkpoint...
Created new classifier: 256 -> 4 classes

Final Evaluation on Test Set


/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))



Test Loss: 0.8483
Test Accuracy: 0.7619

Per-class metrics:
  Cantonese:
    Precision: 0.6667
    Recall: 0.2500
    F1: 0.3636
    Support: 8
  Mandarin:
    Precision: 0.7895
    Recall: 0.9677
    F1: 0.8696
    Support: 31
  Taiwanese:
    Precision: 0.0000
    Recall: 0.0000
    F1: 0.0000
    Support: 2
  Wu:
    Precision: 0.0000
    Recall: 0.0000
    F1: 0.0000
    Support: 1

Macro averages:
  Precision: 0.3640
  Recall: 0.3044
  F1: 0.3083

Weighted averages:
  Precision: 0.7097
  Recall: 0.7619
  F1: 0.7111

Metrics saved to training_output/test_metrics.json
Confusion matrix saved to training_output/confusion_matrix.png

Process Complete!


In [ ]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Sun Dec 14 00:18:56 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA A100-SXM4-80GB          Off |   00000000:00:05.0 Off |                    0 |
| N/A   34C    P0             62W /  400W |   43495MiB /  81920MiB |      0%      Default |
|                                         |                        |             Disabled |
+-----------------------------------------+-----

In [ ]:
import psutil

ram_gb = psutil.virtual_memory().total / 1e9
print('Your runtime has {:.1f} gigabytes of available RAM\n'.format(ram_gb))

if ram_gb < 20:
  print('Not using a high-RAM runtime')
else:
  print('You are using a high-RAM runtime!')

Your runtime has 179.4 gigabytes of available RAM

You are using a high-RAM runtime!


In [ ]:
if torch.cuda.is_available():
    torch.cuda.synchronize()
    torch.cuda.empty_cache()

In [ ]:
if __name__ == "__main__":
    main()